In [67]:
from sklearn.feature_extraction.text import TfidfVectorizer
from konlpy.tag import Okt
import pandas as pd
from tqdm import tqdm

In [68]:
# KoNLPy의 Okt 형태소 분석기 사용
okt = Okt()

In [69]:
def tokenize(text):
    # 형태소 분석을 통해 명사만 추출
    return [word for word in okt.nouns(text) if len(word) > 1]

In [36]:
def get_keywords(text, num=10):
    # TF-IDF 벡터화기 생성
    vectorizer = TfidfVectorizer(tokenizer=tokenize, min_df=1)
    X = vectorizer.fit_transform([text])  # 문자열 전체를 하나의 문서로 처리

    # 단어와 TF-IDF 점수 매핑
    tfidf_scores = X.sum(axis=0).A1
    words = vectorizer.get_feature_names_out()

    # 단어와 TF-IDF 점수를 데이터프레임으로 변환
    tfidf_df = pd.DataFrame({'Word': words, 'TF-IDF Score': tfidf_scores})

    # TF-IDF 점수로 정렬하여 상위 num개 키워드 출력
    return tfidf_df.sort_values(by='TF-IDF Score', ascending=False).head(num)

In [52]:
def extract_keywords_from_documents(documents, top_n=10):
    # TF-IDF 벡터화기 생성
    vectorizer = TfidfVectorizer(tokenizer=tokenize, min_df=1)
    X = vectorizer.fit_transform(documents)
    
    # 단어와 TF-IDF 점수 매핑
    words = vectorizer.get_feature_names_out()
    tfidf_scores = X.toarray()
    
    # 각 문서별 키워드 추출
    keywords_per_document = []
    for i, doc_scores in tqdm(enumerate(tfidf_scores)):
        tfidf_df = pd.DataFrame({'Word': words, 'TF-IDF Score': doc_scores})
        top_keywords = tfidf_df.sort_values(by='TF-IDF Score', ascending=False).head(top_n)
        keywords_per_document.append({
            'Document': i,
            'Keywords': ', '.join(top_keywords['Word'])
        })
    
    return pd.DataFrame(keywords_per_document)

In [126]:
def string_to_list(string):
    # 문자열에서 대괄호와 작은따옴표를 제거하고 쉼표로 구분하여 리스트로 변환
    string_list = string.strip("[]").replace("'", "").split(", ")
    
    return string_list

In [127]:
def add_to_set(s1, s2):
    sl1 = string_to_list(s1)
    sl2 = string_to_list(s2)
    
    return set(sl1+sl2)

In [128]:
def parse_text_file(file_path):
    result_dict = {}

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            # 줄의 앞뒤 공백 제거
            line = line.strip()

            # C?? 형식의 코드와 나머지 문자열 분리
            if line:
                parts = line.split(' ', 1)  # 첫 번째 공백으로 나눔
                if len(parts) == 2:
                    key = parts[0]
                    values = parts[1].split(',')  # 쉼표와 공백으로 구분하여 리스트 생성
                    result_dict[key] = values

    return result_dict

In [129]:
def count_matches(keyword_list, reference_list):
    return sum(1 for keyword in keyword_list if keyword in reference_list)

In [130]:
def count_keyword_matches(keywords, ksic_key):
    result = {} # empty dict
    
    for ksic in ksic_key.items():
        intersect = keywords.intersection(ksic[1])
        if len(intersect) > 0 :
            result[ksic[0]] = intersect
            
    return result

In [131]:
def get_max_ksic(match_set):
    if len(match_set) == 0 :
        return {}
    
    results = {key for key, value in match_set.items() if len(value) >= 3}
    max_set_size = max(len(value) for value in match_set.values())
    results.update({key for key, value in match_set.items() if len(value) == max_set_size})
    
    return results

In [70]:
# 예시 문장
documents = [
    '이낙연 측근이 말하는 ‘치밀한’ 사면론 카드 “결국 문재인 대통령이 어떤 판단을 하느냐에 달렸다. 대통령이 사면을 결정하면 지지층의 반발도 어느 정도 잦아들 가능성이 있다.” 이낙연 더불어민주당 대표가 새해 첫 메시지로 던진 이명박·박근혜 두 전직 대통령 사면 관련 논란에 대한 이 대표 측 한 인사의 말이다. 정치권에선 이 대표 사면론에 대해 비판 일색이었다. 여권 내부에선 ‘사과도 없는 범죄자들을 어떻게 사면하느냐’, ‘특히 박근혜씨는 형사범죄뿐 아니라 국민들의 판단(탄핵)도 있었다’ 등의 의견이 있고, 야권에서도 ‘이낙연 지지율 반등 카드’라는 지적과 함께 김종인 국민의힘 비상대책위원장의 두 전직 대통령 범죄 관련 사과로 환영만 할수 없다는 분위기도 있다. 해당 관계자는 미디어오늘에 “당장은 비난이 많을 수밖에 없고 나도 원론적 입장만 따지면 사면 반대입장이지만 이 대표 입장에선 정치적으로 고려한 결정 아니겠느냐”고 했다. 여기서 ‘정치적 고려’란 문 대통령이 느끼는 정치적 부담과 이 대표 대권 행보를 뜻한다. 문 대통령 입장에선 자신의 임기 직전 두 전직 대통령이 모두 옥에 갇혔고, 박근혜씨의 경우 전직 대통령 중 최장기간(약 3년10개월) 수감 중인데 이는 법적인 문제를 떠나 문 대통령에게 정치적 부담으로 느껴진 게 사실이라고 전했다. 또한 호남 인사로 분류되는 이 대표가 향후 대권행보에서 영남권 지지를 얻을 돌파구이기도 하다는 게 해당 관계자의 설명이다. 이런 가운데 6일 리얼미터·오마이뉴스 여론조사를 보면 두 전직 대통령 사면에 대해 찬성(47.7%)과 반대(48%) 의견은 팽팽했다. 정치권과 언론에서 사면론에 비판적 의견이 지배했던 것과 다른 분위기다. 민주당 지지층에선 반대(88.8%), 국민의힘 지지층에선 찬성(81.4%)이 압도적으로 나타난 것을 봐도 ‘표계산’의 관점에서 볼 때 사면론 카드를 실패했다고 단정하긴 어렵다. 또한 7일 조선일보는 “박근혜는 사면, 이명박은 보류 검토”란 기사에서 ‘여권 핵심 관계자’의 말을 인용해 박근혜씨 사면을 검토한다는 내용을 전했다. 이는 이 대표 쪽 관계자일 가능성이 높다. 조선일보 취재에 청와대 관계자는 “사면 관련 입장이 없다”고 했고, 해당 보도 이후 청와대 대변인은 “사면을 검토한 적 없다”고 했지만 여당 대표가 실제 사면을 건의할 경우 청와대가 이를 일방적으로 외면할 수 없는 것도 사실이다. 이 대표 쪽 관계자는 미디어오늘에 “문 대통령과 이 대표가 지난 연말에 만났는데 그 자리에서 무엇을 논의했는지는 당사자들만 알 수 있다”고 선을 그으면서도 “두분은 서로 어떤 생각을 하는지 알만한 각별한 사이”라며 사전교감 가능성을 열어뒀다. 이 대표는 사면건의와 영수회담 제안에 대해 “대통령과 사전교감이 없었다”고 말해왔다. 사전교감 여부를 떠나 결과적으로 공은 대통령에게 넘어간 분위기다. 문 대통령이 이 대표 건의를 받아들여 사면할 경우 이 대표는 그가 말한대로 ‘대통령에 대한 충정’을 보이면서 동시에 영남·보수성향 지지층에게도 어필하는 두 마리 토끼를 잡게 된다. 문 대통령이 최종적으로 임기 내에 사면을 단행하지 않더라도 이 대표에 대한 메시지를 내놓을 것이란 예상도 가능하다. 여권의 유력 대선주자인 이 대표가 혼자서 소위 ‘쇼’를 한 모양새가 되는 건 정권 입장에서도 부담스러운 일이기 때문이다. 이 대표는 사면 건의를 꺼내든 이유로 ‘국민통합’을 말했다. 이는 총리 시절부터 그가 구상해 온 생각인 만큼 앞으로 국민통합과 관련한 의제를 더 던질 것이라고 해당 관계자는 전했다. 이달 내 진행할 것으로 보이는 문 대통령과 이 대표의 신년기자회견에서 어떤 메시지가 나올지 주목된다.',
    '국민의힘 추미애-문재인까지 고발하자 민주 “황당무계” 국민의힘이 서울동부구치소의 코로나19 감염자 급증 및 사망자 발생 책임을 물어 추미애 법무부장관을 형사고발했다. 국민의힘은 또 윤석열 검찰총장을 불법적으로 징계했다며 추 장관과 함께 문재인 대통령까지 검찰에 고발했다. 이에 더불어민주당은 황당무계하다는 반응을 내놓았다. 이들은 또 기승전-검찰고발이냐며 모든 것을 검찰총장에게 해결해달라고 하느냐고 반문했다. 국민의힘 법제사법위원회 소속 의원들은 6일 오후 기자회견에서 추 장관을 고발한 사유에 대해 “법무부 산하 서울동부구치소의 코로나19 감염자에 대한 격리수용 등을 제대로 관리하지 않아 수용자 인권과 생명을 제대로 지키지 못하고 5일 현재 사망자 1명, 감염자 1085명에 이르게 한 혐의”라고 주장했다. 이들은 “지난해 11월27일 서울동부구치소 직원 1명이 확진 판정을 받은 이후 서울동부치소는 역학조사 및 접촉자 분리를 제대로 실시하지 않고 전수조사 대응이 늦었으며, 최초 확진자 발생 전 마스크도 지급하지 않았다”며 “지난해 9월엔 보건마스크를 자비로 구매하게 허가해 달라는 여주교도소 재소자의 진정을 기각하는 등 수감자들의 생명·신체의 위험을 방치하고 사망자와 감염자를 낳아 업무상과실·중과실치사상, 직무유기 혐의를 저질렀다”고 주장했다. 국민의힘은 “추 장관은 서울동부구치소의 확진자가 700명을 넘어선 지난 12월 29일, 첫 확진자가 나온 지 32일이 지나서야 서울동부구치소를 찾았다”며 “그 전날까지 추 장관은 ‘윤 총장을 탄핵시켜야 한다’는 여당 의원의 글을 SNS에 올리며 연일 윤 총장 찍어내기에 정신이 팔려 있었다”고 비판했다. 문 대통령과 추 장관의 윤석열 검찰총장 징계 건도 고발했다. 국민의힘은 “윤석열 검찰총장에 대한 감찰을 법무부 감찰규정 등 법령에 위반되게 진행했고, 재량권을 일탈하여 직무집행정지처분을 했고, 의사정족수도 못 갖춘 절차상 심각한 하자가 있음에도 추미애 장관과 문재인 대통령은 직권을 남용해 윤 총장 징계를 강행했다”며 “검찰의 철저한 수사를 당부 드린다”고 촉구했다. 이에 더불어민주당은 서울동부구치소 집단감염 비판을 받겠다면서도 고발까지 나선 것은 보복수사에 해당한다고 반발했다. 문 대통령까지 고발한 것 역시 황당무계하다는 반응이다. 김태년 더불어민주당 원내대표는 7일 오전 정책조정회의에서 추 장관 고발을 두고 “이성과 품격을 내던진 야당 고발 정치에 깊은 유감”이라고 밝혔다. 그는 “동부구치소 발 집단 감염 초기 대응은 비판할 수 있고, 추장관도 책임을 통감하며 거듭 사과했다”면서도 “하지만 추장관 고발은 검찰 끌여 들어 보복수사하겠다는 잔인한 정쟁”이라고 비판했다. 김 원내대표는 국민의힘의 추 장관 고발이 처음이 아니라며 울산시장 선거개입 의혹, 아들 병역 관련, 윤석열 징계 추진 등을 들어 “국민의힘이 추 장관에 묻지마 고발 되풀이하고 있다”고 했다. 그는 “국회에서 정치로 해결해야할 일들과 국정운영 사안까지 검찰 고발을 남발했다”며 “정치와 행정 영역 판단을 검찰과 법원에 넘기는 것은 민주주의를 후퇴시키는 행위”라고 비판했다. 김 원내대표는 특히 윤 총장 징계 재가를 빌미로 문 대통령 고발도 나선 것과 관련해서는 “황당무계하다”며 “정치의 금도를 지켜달라”고 했다. 이어 그는 “민주주의의 가드레일 부수는 묻지마 고발을 철회하기 바란다”며 “국민 갈등과 정치 불신을 키우는 무차별적 정쟁 유발에는 단호히 대응하겠다”고 강조했다. 강선우 더불어민주당 대변인도 논평을 내어 국민의힘의 고발 고질병이 또 도졌다며 ‘기승전 고발정치’에 몰두하고 있다고 밝혔다. 강 대변인은 “대통령의 인사권까지 고발하고 나섰다”며 “검찰총장을 앞세워 정치적 이득을 얻어 보려는 속셈인것인지, 아니면 스스로 일을 풀어나갈 힘이 없어 무능함을 고소 고발로 감추려는 것인지 알 수 없다”고 덧붙였다.',
    '윤호중 “인력 전혀 안줄여 놀라” 검찰 개혁 비협조 비판 검찰이 검경 수사권 조정이 됐는데도 기소권 중심의 조직으로 개편하거나 수사권 인력을 전혀 조정하지 않고 있다는 지적이 제기돼 주목된다. 특히 이것이 검찰이 수사권 조정을 흔쾌히 받아들이지 않고 있고, 검찰개혁에 협조하지 않으려는 것 아니냐는 목소리도 나왔다. 윤호중 국회 법제사법위원장은 7일 더불어민주당 당대표 회의실에서 열린 ‘더불어민주당 검찰개혁특위 3차회의’에서 이같이 전했다. 윤 위원장은 특위 출범 후 엊그제 2차회의에서 검경 수사권 조정후 검찰의 이행 상황 현황을 점검한 결과 “검찰개혁특위를 즉각 가동해 중단없는 2단계 검찰개혁에 착수한 일을 정말 잘했구나라고 확인했다”고 지적했다. 그 이유를 두고 윤 위원장은 “검찰이 직접 수사해오던 범위가 대폭 축소돼 6대 범죄 중에서도 중대 규모 범죄에 대해서만 수사하게 돼 있고 검찰의 직접 수사건수도 4분의 1 이하로 줄어들게 됐는데도 검찰은 그동안 운영해왔던 검찰 수사 인력을 전혀 조정하지 않고 있었다”며 “수사권이 줄었으니 기소권을 중심으로 운영하려면 기소권 중심으로 개편해야 하는데, 이 또한 전혀 이뤄지지 않고 있었다”고 전했다. 윤 위원장은 위원들이 다들 굉장히 놀랐다며 “검찰은 지금도 검찰 수사권 조정을 흔쾌히 받아들이고 있지 않은 상황이었다”고 평가했다. 윤 위원장은 “국회가 법 개정으로 검찰개혁을 추진해왔고 앞으로 해나갈텐데 검찰이 적극 협조하려는 의사 있는지 의심하지 않을 수 없다”며 “더욱더 검찰개혁에 매진해야겠다는 그런 사실을 확인했다”고 강조했다. 윤 위원장은 향후 검찰개혁 특위가 입법과제를 발굴해 오는 2월 초까지 입법안을 마련해 국회에 제출할 예정이라고 덧붙였다. 이낙연 더불어민주당 대표는 지난해 검경수사권 조정을 통해 6대 범죄만 검찰이 직접 수사하도록 하는 형사소송법 개정한 것을 들어 “개정 형사소송법이 1일부터 이미 시행되고 있다”고 전했다. 이 대표는 이와 함께 공수처 출범이 검찰의 기소독점에 예외를 만드는 70년 형사사법 역사가 새로운 변화를 맞는다고도 평가했다. 이어 이 대표는 검찰의 기소와 수사권 분리를 두고 “불공정한 수사와 선택적 기소를 포함한 검찰권 남용 방지를 포함해 검찰개혁의 추가 과제를 신속하고 과감하게 이행해 나가야 한다”며 “검찰청법과 형소법 개정안을 다음달 2월까지 국회 제출하고 그 안을 토대로 검찰개혁 추가 과제를 신속 착실하게 추진해가도록 하겠다”고 밝혔다. 이 대표는 “제도에 못지 않게 조직 문화나 구성원 의식 변화 수반돼야 한다”며 “할 수 있다면 그런 문제까지 포함해서 검찰이 문자 그대로 국민의 검찰 성숙한 민주검찰로 거듭나도록 해야 한다”고 촉구했다.',
]

In [71]:
tokenize(documents[0])

['이낙연',
 '측근',
 '사면',
 '카드',
 '문재인',
 '대통령',
 '판단',
 '대통령',
 '사면',
 '결정',
 '지층',
 '반발',
 '정도',
 '아들',
 '가능성',
 '이낙연',
 '민주당',
 '대표',
 '새해',
 '메시지',
 '이명박',
 '박근혜',
 '전직',
 '대통령',
 '사면',
 '관련',
 '논란',
 '대한',
 '대표',
 '인사',
 '정치권',
 '대표',
 '사면',
 '대해',
 '비판',
 '일색',
 '여권',
 '내부',
 '사과',
 '범죄자',
 '사면',
 '박근혜',
 '형사',
 '범죄',
 '국민',
 '판단',
 '탄핵',
 '의견',
 '야권',
 '이낙연',
 '지지율',
 '반등',
 '카드',
 '지적',
 '김종인',
 '국민',
 '비상',
 '대책',
 '위원장',
 '전직',
 '대통령',
 '범죄',
 '관련',
 '사과',
 '환영',
 '분위기',
 '해당',
 '관계자',
 '미디어오늘',
 '당장',
 '비난',
 '원론',
 '입장',
 '사면',
 '입장',
 '대표',
 '입장',
 '정치',
 '고려',
 '결정',
 '여기',
 '정치',
 '고려',
 '대통령',
 '정치',
 '부담',
 '대표',
 '대권',
 '행보',
 '대통령',
 '입장',
 '자신',
 '임기',
 '직전',
 '전직',
 '대통령',
 '모두',
 '박근혜',
 '경우',
 '전직',
 '대통령',
 '장기간',
 '개월',
 '수감',
 '법적',
 '문제',
 '대통령',
 '정치',
 '부담',
 '사실',
 '또한',
 '호남',
 '인사',
 '분류',
 '대표',
 '향후',
 '대권',
 '행보',
 '영남권',
 '지지',
 '돌파구',
 '해당',
 '관계자',
 '설명',
 '가운데',
 '리얼미터',
 '오마이',
 '뉴스',
 '여론조사',
 '전직',
 '대통령',
 '사면',
 '대해',
 '찬성',
 '반대',
 '의견',
 '팽팽했다'

In [75]:
keys = extract_keywords_from_documents([documents[0]], 20)

1it [00:00, 1221.05it/s]


In [81]:
keys.iloc[0].Keywords

'사면, 대통령, 대표, 관계자, 입장, 박근혜, 전직, 국민, 건의, 지층, 관련, 정치, 해당, 분위기, 이낙연, 청와대, 대해, 대한, 카드, 메시지'

In [37]:
get_keywords(documents[0], 10)

Word  TF-IDF Score
70    사면      0.470759
32   대통령      0.444606
33    대표      0.444606
10   관계자      0.183073
117   입장      0.156920
53   박근혜      0.130766
121   전직      0.130766
14    국민      0.130766
4     건의      0.104613
135   지층      0.104613

In [38]:
get_keywords(documents[1], 10)

Word  TF-IDF Score
12    고발      0.545951
116   장관      0.300273
20    국민      0.272976
41    동부      0.218380
127   정치      0.191083
19   구치소      0.191083
2     감염      0.163785
38   대통령      0.163785
9     검찰      0.163785
145   징계      0.136488

In [39]:
get_keywords(documents[2], 10)

Word  TF-IDF Score
9     검찰      0.742869
5     개혁      0.275137
59   수사권      0.220109
86    조정      0.192596
68   위원장      0.165082
58    수사      0.137568
28    대표      0.137568
105   특위      0.110055
17    국회      0.110055
80    전혀      0.110055

In [8]:
# TF-IDF 벡터화기 생성
vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform(documents)

In [9]:
# 단어와 TF-IDF 점수 매핑
tfidf_scores = X.sum(axis=0).A1
words = vectorizer.get_feature_names_out()

In [10]:
# 단어와 TF-IDF 점수를 데이터프레임으로 변환
tfidf_df = pd.DataFrame({'Word': words, 'TF-IDF Score': tfidf_scores})

In [11]:
# TF-IDF 점수로 정렬하여 상위 10개 키워드 출력
top_keywords = tfidf_df.sort_values(by='TF-IDF Score', ascending=False).head(10)
print(top_keywords)

     Word  TF-IDF Score
428   수사권      0.282836
74    검찰이      0.282836
229    대표      0.277266
227  대통령이      0.237657
521  위원장은      0.235697
231   대표는      0.233775
61     검찰      0.210494
384    사면      0.198047
612    전직      0.198047
230   대표가      0.198047


In [13]:
tfidf_df

Word  TF-IDF Score
0     1085명에      0.044108
1     11월27일      0.044108
2        12월      0.044108
3         1명      0.044108
4        1명이      0.044108
..       ...           ...
796  황당무계하다는      0.088216
797    회의실에서      0.047139
798    후퇴시키는      0.044108
799      흔쾌히      0.094279
800       힘이      0.044108

[801 rows x 2 columns]

In [29]:
documents[2]

'윤호중 “인력 전혀 안줄여 놀라” 검찰 개혁 비협조 비판 검찰이 검경 수사권 조정이 됐는데도 기소권 중심의 조직으로 개편하거나 수사권 인력을 전혀 조정하지 않고 있다는 지적이 제기돼 주목된다. 특히 이것이 검찰이 수사권 조정을 흔쾌히 받아들이지 않고 있고, 검찰개혁에 협조하지 않으려는 것 아니냐는 목소리도 나왔다. 윤호중 국회 법제사법위원장은 7일 더불어민주당 당대표 회의실에서 열린 ‘더불어민주당 검찰개혁특위 3차회의’에서 이같이 전했다. 윤 위원장은 특위 출범 후 엊그제 2차회의에서 검경 수사권 조정후 검찰의 이행 상황 현황을 점검한 결과 “검찰개혁특위를 즉각 가동해 중단없는 2단계 검찰개혁에 착수한 일을 정말 잘했구나라고 확인했다”고 지적했다. 그 이유를 두고 윤 위원장은 “검찰이 직접 수사해오던 범위가 대폭 축소돼 6대 범죄 중에서도 중대 규모 범죄에 대해서만 수사하게 돼 있고 검찰의 직접 수사건수도 4분의 1 이하로 줄어들게 됐는데도 검찰은 그동안 운영해왔던 검찰 수사 인력을 전혀 조정하지 않고 있었다”며 “수사권이 줄었으니 기소권을 중심으로 운영하려면 기소권 중심으로 개편해야 하는데, 이 또한 전혀 이뤄지지 않고 있었다”고 전했다. 윤 위원장은 위원들이 다들 굉장히 놀랐다며 “검찰은 지금도 검찰 수사권 조정을 흔쾌히 받아들이고 있지 않은 상황이었다”고 평가했다. 윤 위원장은 “국회가 법 개정으로 검찰개혁을 추진해왔고 앞으로 해나갈텐데 검찰이 적극 협조하려는 의사 있는지 의심하지 않을 수 없다”며 “더욱더 검찰개혁에 매진해야겠다는 그런 사실을 확인했다”고 강조했다. 윤 위원장은 향후 검찰개혁 특위가 입법과제를 발굴해 오는 2월 초까지 입법안을 마련해 국회에 제출할 예정이라고 덧붙였다. 이낙연 더불어민주당 대표는 지난해 검경수사권 조정을 통해 6대 범죄만 검찰이 직접 수사하도록 하는 형사소송법 개정한 것을 들어 “개정 형사소송법이 1일부터 이미 시행되고 있다”고 전했다. 이 대표는 이와 함께 공수처 출범이 검찰의 기소독점에 예외를 만드는 70년 형사사법

In [31]:
# TF-IDF 벡터화기 생성
vectorizer = TfidfVectorizer(tokenizer=tokenize, min_df=1)
X = vectorizer.fit_transform([documents[0]])

In [32]:
# 단어와 TF-IDF 점수 매핑
tfidf_scores = X.sum(axis=0).A1
words = vectorizer.get_feature_names_out()

In [33]:
# 단어와 TF-IDF 점수를 데이터프레임으로 변환
tfidf_df = pd.DataFrame({'Word': words, 'TF-IDF Score': tfidf_scores})

In [35]:
# TF-IDF 점수로 정렬하여 상위 10개 키워드 출력
top_keywords = tfidf_df.sort_values(by='TF-IDF Score', ascending=False).head(10)
print(top_keywords)

    Word  TF-IDF Score
70    사면      0.470759
32   대통령      0.444606
33    대표      0.444606
10   관계자      0.183073
117   입장      0.156920
53   박근혜      0.130766
121   전직      0.130766
14    국민      0.130766
4     건의      0.104613
135   지층      0.104613


In [24]:
documents

['이낙연 측근이 말하는 ‘치밀한’ 사면론 카드 “결국 문재인 대통령이 어떤 판단을 하느냐에 달렸다. 대통령이 사면을 결정하면 지지층의 반발도 어느 정도 잦아들 가능성이 있다.” 이낙연 더불어민주당 대표가 새해 첫 메시지로 던진 이명박·박근혜 두 전직 대통령 사면 관련 논란에 대한 이 대표 측 한 인사의 말이다. 정치권에선 이 대표 사면론에 대해 비판 일색이었다. 여권 내부에선 ‘사과도 없는 범죄자들을 어떻게 사면하느냐’, ‘특히 박근혜씨는 형사범죄뿐 아니라 국민들의 판단(탄핵)도 있었다’ 등의 의견이 있고, 야권에서도 ‘이낙연 지지율 반등 카드’라는 지적과 함께 김종인 국민의힘 비상대책위원장의 두 전직 대통령 범죄 관련 사과로 환영만 할수 없다는 분위기도 있다. 해당 관계자는 미디어오늘에 “당장은 비난이 많을 수밖에 없고 나도 원론적 입장만 따지면 사면 반대입장이지만 이 대표 입장에선 정치적으로 고려한 결정 아니겠느냐”고 했다. 여기서 ‘정치적 고려’란 문 대통령이 느끼는 정치적 부담과 이 대표 대권 행보를 뜻한다. 문 대통령 입장에선 자신의 임기 직전 두 전직 대통령이 모두 옥에 갇혔고, 박근혜씨의 경우 전직 대통령 중 최장기간(약 3년10개월) 수감 중인데 이는 법적인 문제를 떠나 문 대통령에게 정치적 부담으로 느껴진 게 사실이라고 전했다. 또한 호남 인사로 분류되는 이 대표가 향후 대권행보에서 영남권 지지를 얻을 돌파구이기도 하다는 게 해당 관계자의 설명이다. 이런 가운데 6일 리얼미터·오마이뉴스 여론조사를 보면 두 전직 대통령 사면에 대해 찬성(47.7%)과 반대(48%) 의견은 팽팽했다. 정치권과 언론에서 사면론에 비판적 의견이 지배했던 것과 다른 분위기다. 민주당 지지층에선 반대(88.8%), 국민의힘 지지층에선 찬성(81.4%)이 압도적으로 나타난 것을 봐도 ‘표계산’의 관점에서 볼 때 사면론 카드를 실패했다고 단정하긴 어렵다. 또한 7일 조선일보는 “박근혜는 사면, 이명박은 보류 검토”란 기사에서 ‘여권 핵심 관계자’의 말을 인용해 박근혜씨 사

In [42]:
directory_path = '/home/osung/data/korean/modu/json'

In [43]:
df = pd.read_csv(directory_path+'/combined_news.tsv', sep='\t')

In [44]:
len(df)

3611424

In [45]:
df.columns

Index(['id', 'topic', 'text'], dtype='object')

In [46]:
documents = df.text

In [47]:
type(documents)

pandas.core.series.Series

In [48]:
docs = documents[:100]

In [49]:
docs

0     "대통령, 시장 방문만 하지 말고 실천해달라" 2008년의 마지막 새벽, 언론의 카...
1     진성호 의원, 겨우 이 정도였나 오늘(31일) 한나라당 의원 총회에서 조선일보 출신...
2     "소의 해, 정치인들 싸움 좀 그만하시죠" 지난해 12월 31일 대구국채보상기념운동...
3     'MB악법 저지' 촛불 들고 새해 맞은 대전시민들 촛불의 물결이 전국을 뒤 덮었던 ...
4     산(酸) 몰아내니 누이 좋고 매부 좋고 겨울철 우리의 입맛을 돋우는 먹을거리 가운데...
                            ...                        
95    민주당, 12일만에 본회의장 농성 해제 민주당 12일만에 본회의장 농성 해제 민주당...
96    천안시 부당 행정 무더기 적발 계약 체결 부적정, 공사 설계 부적정, 보조금 정산검...
97    일부 반대 속 안양 만안뉴타운 지원센터 열어 안양시와 경기도시공사는 만안 뉴타운사업...
98    2009년의 길목에서 연말을 보내고 새해를 맞이하면서도 대다수 사람들의 마음은 그리...
99    비정규직 방송작가들도 "방송법 개악 반대" 전국언론노동조합의 총파업이 열흘 넘게 이...
Name: text, Length: 100, dtype: object

In [66]:
keywords = extract_keywords_from_documents(documents)

KeyboardInterrupt: 

In [53]:
keywords

Document                                      Keywords
0          0   가락시장, 가명, 수산시장, 배추, 상인, 수산물, 새벽, 생선, 채소, 도매
1          1  의원, 망언, 조선일보, 최소한, 라면, 진성호, 국민, 국회의원, 구태, 인간
2          2       시민, 일찍, 공원, 대구, 국채, 경제, 기념, 보상, 정치인, 맞이
3          3    대전, 시민, 촛불, 악법, 촛불집회, 정이, 이명박, 노래, 대학생, 언론
4          4      어민, 김양, 생산, 장흥, 양식, 무산, 잡태, 소비자, 어장, 생산량
..       ...                                           ...
95        95    민주당, 본회의, 민생, 법안, 국민, 농성, 대표, 직권상정, 처리, 합의
96        96     감사, 천안시, 소홀, 설치, 개인정보, 시설, 조치, 통지, 적발, 편의
97        97    뉴타운, 사업, 시공사, 주민, 경기도, 안양, 센터, 재정, 안양시, 지역
98        98       계층, 정책, 주민, 정치인, 사회, 이익, 대한, 예산, 단체, 한계
99        99  작가, 총파업, 언론, 마산, 언론노조, 지지, 입맛, 비정규직, 국민, 정규직

[100 rows x 2 columns]

In [54]:
docs[0]

'"대통령, 시장 방문만 하지 말고 실천해달라" 2008년의 마지막 새벽, 언론의 카메라는 서울 여의도를 향했다. 방송법 등 주요쟁점 법안이 상정될 국회 본회의장을 두고 여야 의원들의 전쟁을 기다리고 있었던 것. 같은 시각, 국회 밖 세상에서 서민들은 경제 위기와 강추위 속에서 삶의 고단함과 정치에 대한 절망감에 맞선 채 팍팍한 삶을 이어가고 있었다. 이들의 목소리를 듣기 위해 이날 새벽 3시 대한민국의 아침을 여는 서울 가락동 농수산물종합도매시장으로 향했다. 가락시장으로 가는 택시 안에서 2008년의 마지막 새벽을 맞는 서민들의 얘기를 엿들을 수 있었다. 택시기사 서인철(가명·63)씨는 말한다. "LPG값이 휘발유보다 비싸졌고, 9만9000원 하는 사납금 내기도 벅차다. (한 달에) 100만원도 벌기 힘들다. 40년 동안 택시기사를 했는데, 요즘이 제일 힘들다. 택시 손님 열에 아홉은 힘들다고 한다. 더 암울한 건 내년엔 더 어렵다는 거다. 정치인들? 멱살 잡고 싸우는 거 말고 뭘 하나? 이젠 짜증내기도 귀찮다." 치열한 삶터, 가락시장에 드리워진 불황의 그림자 새벽 3시 30분, 가락시장의 첫인상은 그야말로 치열한 삶터였다. 가락시장 인근 도로엔 농수산물을 싣고 전국에서 올라온 트럭들이 \'차산차해\'를 이뤘다. 가락시장 안에는 트럭과 함께 짐을 옮기는 지게차·오토바이·손수레로 가득 차 더욱 복잡했다. 가락시장 수산시장에서는 방어 경매가 한창이었다. 중개인이 일반인들이 알아듣기 힘든 말로 몇 차례 중얼거리자 경매는 이내 끝났다. 방어는 어찌나 힘이 좋은지 한 번 몸을 뒤집자 바구니 밖 3~4m까지 물이 튈 정도였다. 상인들도 방어만큼이나 바삐 움직였다. 사람들은 분주히 수산물을 날랐다. 경매로 수산물을 산 중간도매상들은 좌판을 펼쳐놓고 손님들을 기다렸다. 그들은 머리엔 모자·스카프 등을 두르고, 신발은 털장화를 싣고는 난로 옆에 바싹 붙어 생선 손질을 하고 있었다. 쪼그리고 앉아 고등어 배를 가르고 있던 김진숙(가명·51)씨의 표정엔 노곤함이 묻어났다. 전

In [65]:
get_keywords(docs[0])

Word  TF-IDF Score
93     사람      0.305852
4    가락시장      0.244682
99     새벽      0.214096
5      가명      0.214096
121    시장      0.214096
116  수산시장      0.183511
82     배추      0.183511
115   수산물      0.152926
102    생선      0.152926
97     상인      0.152926

In [63]:
docs[5]

'"방송장악은 군사독재로 회귀하는 것" 한나라당이 추진 중인 언론법과 관련해 언론노조의 총파업, 지역방송까지 가세하여 언론법 상정을 저지하기 위한 시민홍보전과 촛불문화제가 잇따르고 있다. 지난 12월 31일 송구영신이 펼쳐지는 제야의 타종식에 앞서 국채보상운동기념공원과 한일극장 앞에서 대구MBC, 시한부 파업에 돌입한 대구CBS 방송국 언론노조 소속의 100여 명의 기자들과 시민단체 회원들이 참가해 촛불문화제를 가졌다. 대구MBC 소속 노조원 100여 명은 전국언론노조의 지침에 맞춰 지난 26일 오전 6시를 통해 전면 파업에 돌입했고, 대구CBS는 시한부 파업을 통해 정부의 언론정책을 성토했다. 이득재 대구가톨릭대학교 교수(러시아어과)는 찬조발언을 통해 "전교조 해체, 일제고사 부활, 뉴라이트의 역사문제, 국정원 강화 등은 파시즘 체제를 고집하는 것이 아니고 무엇인가?"라고 되물었다. 이 교수는 "조중동이 언론에 80%를 지배하고 있으니 KBS, YTN에 MBC도 방송 장악 수순을 통해 군사독재로 회귀하는 것, 이러한 것이 민간파쇼 체제나 다를 바 없다"며 정부의 언론정책을 강하게 비난했다. 강금수 대구참여연대 사무처장은 "방송법 개악의 핵심적인 문제점은 조·중·동과 같은 족벌신문들이 방송까지도 소유할 수 있도록 하는 것이기에 친정부적, 친재벌적인 성향을 보이게 된 그들(조·중·동을 의미)이 것을 다 장악하게 되면 편향된 보도, 언론의 공정보도가 훼손될 것을 우려하고 있다"고 말했다. 정부의 언론정책에 대해 조명래 시당위원장(진보신당대구시당)도 "국민의 방송, 공영방송이 재벌에 넘어가게 되면 자본의 논리(돈, 재벌 등)로 방송을 보기 때문에 공익적인 부분은 사라질 것이다"고 주장했다. 그는 정부의 언론 민영화 정책은 "현재 한나라당과 이명박 정부의 정권 연장의 도구로 볼 수밖에 없기에 국민과 힘을 합쳐 반드시 막아야 할 일이다"고 강조했다. 이영대 대구MBC노조위원장은 "우리가 지금 싸우고 있는 것은 민주주의의 위기가 닥쳐왔기 때문이다"고 파업 각오를 밝히면서

In [64]:
df.topic[:100]

0     사회
1     사회
2     사회
3     사회
4     사회
      ..
95    정치
96    사회
97    사회
98    사회
99    사회
Name: topic, Length: 100, dtype: object

In [82]:
directory_path = '/home/osung/data/korean/modu/json'
df = pd.read_csv(directory_path+'/combined_news_P.tsv', sep='\t')

In [95]:
extract_keywords_from_documents([df.text[0]]).Keywords

1it [00:00, 1094.83it/s]


0    대통령, 라며, 개혁, 녹색, 일자리, 정부, 지원, 강조, 산업, 제정부
Name: Keywords, dtype: object

In [84]:
df.text[:10]

0    이명박 대통령, '비상경제정부' 선언 이명박 대통령이 '비상경제정부'를 선언하고 나...
1    홍준표는 왜 회담장을 박차고 나왔나 국회 대치정국을 풀기 위한 여야의 최후 담판 과...
2    "저널리즘 차원에서 중요한 사건틀리다고 생각했다면 말도 안 했다" MBC <뉴스데스...
3    "MBC가 일부 재벌과 언론사 소유가 된다면..." <뉴스데스크> 박혜진 아나운서,...
4    문순씨네 블로그? 국회의원도 현장중계 국회의원도 이젠 블로거? 최문순 의원이 만든 ...
5    MB의 '비상경제정부' 윤곽 드러나다 이명박 정부가 경제위기를 조기에 극복하기 위해...
6    자치단체 소식지, 선거법 위반 논란 대전시와 각 구청에서 발행하는 소식지(홍보물)는...
7    KBS, '경인운하 경제성 있다'는 정부 입장 힘 실어 1. 방송3사, 국회 파행 ...
8    민주당, 12일만에 본회의장 농성 해제 민주당 12일만에 본회의장 농성 해제 민주당...
9    이문열 "권력 놓은 홍위병들, 각 분야에서 저항" 대표적인 보수논객 작가 이문열씨가...
Name: text, dtype: object

In [93]:
get_keywords(df.text[0]).Word

104    대통령
119     라며
16      개혁
82      녹색
261    일자리
288     정부
315     지원
10      강조
172     산업
295    제정부
Name: Word, dtype: object

In [ ]:
p_keywords = []

for doc in tqdm(df.text) :
    p_keywords.append(extract_keywords_from_documents([doc]).Keywords)

  0%|                                                | 0/555588 [00:00<?, ?it/s]
1it [00:00, 998.88it/s]
  0%|                                     | 1/555588 [00:00<53:41:19,  2.87it/s]
1it [00:00, 1143.80it/s]
  0%|                                     | 2/555588 [00:00<69:01:00,  2.24it/s]
1it [00:00, 1469.11it/s]

1it [00:00, 1741.82it/s]

1it [00:00, 318.06it/s]
  0%|                                     | 5/555588 [00:00<23:55:56,  6.45it/s]
1it [00:00, 1707.08it/s]

1it [00:00, 457.24it/s]
  0%|                                     | 7/555588 [00:01<25:43:00,  6.00it/s]
1it [00:00, 1122.97it/s]
  0%|                                     | 8/555588 [00:01<38:06:41,  4.05it/s]
1it [00:00, 1148.50it/s]
  0%|                                     | 9/555588 [00:02<59:18:07,  2.60it/s]
1it [00:00, 1588.15it/s]

1it [00:00, 1702.23it/s]

1it [00:00, 1339.61it/s]
  0%|                                    | 12/555588 [00:02<32:47:46,  4.71it/s]
0it [00:00, ?it/s]
1it [00:00,  4.63it/s]

1it [00

  0%|                                   | 214/555588 [00:53<34:29:52,  4.47it/s]
0it [00:00, ?it/s]
1it [00:00,  4.16it/s]
  0%|                                   | 215/555588 [00:53<37:13:32,  4.14it/s]
1it [00:00, 1332.37it/s]

1it [00:00, 1607.01it/s]

0it [00:00, ?it/s]
1it [00:00,  4.96it/s]
  0%|                                   | 218/555588 [00:54<38:38:06,  3.99it/s]
1it [00:00, 1467.05it/s]

1it [00:00, 1564.46it/s]

1it [00:00, 1682.43it/s]
  0%|                                   | 221/555588 [00:54<26:32:40,  5.81it/s]
0it [00:00, ?it/s]
1it [00:00,  5.04it/s]
  0%|                                   | 222/555588 [00:55<43:27:57,  3.55it/s]
1it [00:00, 1296.14it/s]

1it [00:00, 506.31it/s]
  0%|                                   | 224/555588 [00:56<38:41:12,  3.99it/s]
1it [00:00, 1247.19it/s]
  0%|                                   | 225/555588 [00:56<39:57:31,  3.86it/s]
1it [00:00, 1433.46it/s]

1it [00:00, 1150.39it/s]
  0%|                                   | 227/555588

  0%|                                   | 444/555588 [01:45<36:05:51,  4.27it/s]
1it [00:00, 1155.46it/s]
  0%|                                   | 445/555588 [01:46<52:52:37,  2.92it/s]
1it [00:00, 1080.17it/s]
  0%|                                   | 446/555588 [01:46<53:10:45,  2.90it/s]
1it [00:00, 731.86it/s]
  0%|                                   | 447/555588 [01:46<50:43:56,  3.04it/s]
1it [00:00, 1262.58it/s]
  0%|                                   | 448/555588 [01:47<49:14:17,  3.13it/s]
1it [00:00, 717.22it/s]

1it [00:00, 1268.69it/s]
  0%|                                   | 450/555588 [01:47<49:19:22,  3.13it/s]
1it [00:00, 1170.94it/s]
  0%|                                   | 451/555588 [01:48<49:49:15,  3.10it/s]
1it [00:00, 1335.34it/s]

1it [00:00, 613.11it/s]
  0%|                                   | 453/555588 [01:48<46:57:06,  3.28it/s]
1it [00:00, 1458.38it/s]

1it [00:00, 848.53it/s]
  0%|                                   | 455/555588 [01:48<33:33:25,  4.60it/

  0%|                                   | 658/555588 [02:41<26:49:17,  5.75it/s]
1it [00:00, 1158.65it/s]

1it [00:00, 527.32it/s]
  0%|                                   | 660/555588 [02:42<35:06:18,  4.39it/s]
1it [00:00, 1093.98it/s]

1it [00:00, 1126.59it/s]
  0%|                                   | 662/555588 [02:43<38:19:20,  4.02it/s]
1it [00:00, 1506.57it/s]

1it [00:00, 590.08it/s]
  0%|                                   | 664/555588 [02:43<34:41:30,  4.44it/s]
1it [00:00, 832.37it/s]

1it [00:00, 1200.77it/s]
  0%|                                   | 666/555588 [02:44<37:17:17,  4.13it/s]
1it [00:00, 1309.49it/s]

1it [00:00, 624.71it/s]
  0%|                                   | 668/555588 [02:44<29:23:10,  5.25it/s]
1it [00:00, 1005.11it/s]

1it [00:00, 474.15it/s]
  0%|                                   | 670/555588 [02:44<29:29:45,  5.23it/s]
1it [00:00, 1291.35it/s]
  0%|                                   | 671/555588 [02:44<31:41:16,  4.86it/s]
1it [00:00, 1493.17it/s]



  0%|                                   | 875/555588 [03:38<61:08:56,  2.52it/s]
1it [00:00, 1057.57it/s]

1it [00:00, 1164.44it/s]

1it [00:00, 1712.66it/s]
  0%|                                   | 878/555588 [03:38<33:13:04,  4.64it/s]
1it [00:00, 1184.16it/s]

1it [00:00, 1410.80it/s]
  0%|                                   | 880/555588 [03:39<37:29:54,  4.11it/s]
0it [00:00, ?it/s]
1it [00:00,  4.65it/s]
  0%|                                   | 881/555588 [03:39<38:40:22,  3.98it/s]
1it [00:00, 778.02it/s]

1it [00:00, 887.12it/s]
  0%|                                   | 883/555588 [03:40<40:31:53,  3.80it/s]
1it [00:00, 956.73it/s]

1it [00:00, 557.23it/s]
  0%|                                   | 885/555588 [03:40<49:51:25,  3.09it/s]
1it [00:00, 1368.01it/s]

1it [00:00, 1415.08it/s]
  0%|                                   | 887/555588 [03:41<36:54:55,  4.17it/s]
1it [00:00, 1810.23it/s]

1it [00:00, 1736.05it/s]

1it [00:00, 1279.14it/s]
  0%|                                

...

1it [00:00,  4.50it/s]
 18%|█████▌                        | 102283/555588 [5:20:57<21:33:34,  5.84it/s]
0it [00:00, ?it/s]
1it [00:00,  4.34it/s]

1it [00:00, 1416.52it/s]
 18%|█████▌                        | 102285/555588 [5:20:58<32:16:06,  3.90it/s]
1it [00:00, 1534.13it/s]

1it [00:00, 1829.98it/s]

1it [00:00, 1546.57it/s]
 18%|█████▌                        | 102288/555588 [5:20:58<22:41:02,  5.55it/s]
1it [00:00, 1272.93it/s]

1it [00:00, 1732.47it/s]
 18%|█████▌                        | 102290/555588 [5:20:59<33:22:04,  3.77it/s]
1it [00:00, 1674.37it/s]

1it [00:00, 874.36it/s]

1it [00:00, 890.13it/s]
 18%|█████▌                        | 102293/555588 [5:20:59<23:36:05,  5.34it/s]
1it [00:00, 1829.98it/s]

1it [00:00, 1885.08it/s]

1it [00:00, 1909.11it/s]

1it [00:00, 453.83it/s]
 18%|█████▌                        | 102297/555588 [5:21:00<24:45:44,  5.08it/s]
0it [00:00, ?it/s]
1it [00:00,  4.65it/s]

1it [00:00, 1346.92it/s]
 18%|█████▌                        | 102299/555588

 18%|█████▌                        | 102566/555588 [5:21:57<31:06:47,  4.04it/s]
1it [00:00, 1753.47it/s]

1it [00:00, 1850.97it/s]

1it [00:00, 466.50it/s]
 18%|█████▌                        | 102569/555588 [5:21:58<32:42:02,  3.85it/s]
1it [00:00, 1639.68it/s]

1it [00:00, 1825.99it/s]

0it [00:00, ?it/s]
1it [00:00,  4.23it/s]
 18%|█████▌                        | 102572/555588 [5:21:58<26:22:18,  4.77it/s]
1it [00:00, 1378.80it/s]

1it [00:00, 1408.90it/s]
 18%|█████▌                        | 102574/555588 [5:21:58<21:44:06,  5.79it/s]
1it [00:00, 1743.99it/s]

1it [00:00, 1873.29it/s]

1it [00:00, 455.36it/s]
 18%|█████▌                        | 102577/555588 [5:21:59<26:20:14,  4.78it/s]
1it [00:00, 1638.40it/s]

1it [00:00, 1911.72it/s]

1it [00:00, 1960.87it/s]

1it [00:00, 1276.03it/s]
 18%|█████▌                        | 102581/555588 [5:21:59<20:18:16,  6.20it/s]
1it [00:00, 1603.33it/s]

0it [00:00, ?it/s]
1it [00:00,  4.49it/s]
 18%|█████▌                        | 102583/55

 19%|█████▌                        | 102849/555588 [5:22:57<27:44:52,  4.53it/s]
0it [00:00, ?it/s]
1it [00:00,  4.45it/s]

1it [00:00, 821.45it/s]
 19%|█████▌                        | 102851/555588 [5:22:58<37:22:01,  3.37it/s]
1it [00:00, 1860.00it/s]

1it [00:00, 1848.53it/s]

1it [00:00, 1855.89it/s]

1it [00:00, 1859.18it/s]
 19%|█████▌                        | 102855/555588 [5:22:58<23:23:28,  5.38it/s]
1it [00:00, 1925.76it/s]

1it [00:00, 1283.84it/s]
 19%|█████▌                        | 102857/555588 [5:22:59<33:24:19,  3.76it/s]
0it [00:00, ?it/s]
1it [00:00,  4.46it/s]

1it [00:00, 814.59it/s]
 19%|█████▌                        | 102859/555588 [5:23:00<30:47:50,  4.08it/s]
1it [00:00, 1516.38it/s]

1it [00:00, 1671.70it/s]

1it [00:00, 486.30it/s]
 19%|█████▌                        | 102862/555588 [5:23:00<32:23:06,  3.88it/s]
1it [00:00, 1569.72it/s]

1it [00:00, 1816.50it/s]

1it [00:00, 1867.46it/s]

1it [00:00, 1329.41it/s]
 19%|█████▌                        | 102866/555


1it [00:00, 1922.23it/s]

1it [00:00, 1831.57it/s]

1it [00:00, 1118.18it/s]
 19%|█████▌                        | 102999/555588 [5:23:28<30:38:02,  4.10it/s]
1it [00:00, 1592.37it/s]

1it [00:00, 1739.65it/s]

1it [00:00, 886.75it/s]
 19%|█████▌                        | 103002/555588 [5:23:28<22:42:23,  5.54it/s]
1it [00:00, 1780.26it/s]

1it [00:00, 1840.41it/s]

1it [00:00, 1874.13it/s]

1it [00:00, 476.63it/s]
 19%|█████▌                        | 103006/555588 [5:23:29<24:26:47,  5.14it/s]
1it [00:00, 1617.55it/s]

1it [00:00, 1854.25it/s]

1it [00:00, 1886.78it/s]

1it [00:00, 1293.34it/s]
 19%|█████▌                        | 103010/555588 [5:23:30<19:48:40,  6.35it/s]
1it [00:00, 1612.57it/s]

1it [00:00, 1814.15it/s]

1it [00:00, 1871.62it/s]

1it [00:00, 486.18it/s]
 19%|█████▌                        | 103014/555588 [5:23:31<22:28:05,  5.60it/s]
1it [00:00, 1463.98it/s]

1it [00:00, 1800.13it/s]

1it [00:00, 1143.49it/s]
 19%|█████▌                        | 103017/555588 [5:23:

1it [00:00, 1293.74it/s]
 19%|█████▌                        | 103279/555588 [5:24:31<32:25:25,  3.87it/s]
1it [00:00, 429.48it/s]

1it [00:00, 1239.09it/s]
 19%|█████▌                        | 103281/555588 [5:24:31<26:32:29,  4.73it/s]
1it [00:00, 1231.81it/s]

1it [00:00, 843.08it/s]
 19%|█████▌                        | 103283/555588 [5:24:32<36:57:28,  3.40it/s]
1it [00:00, 1419.39it/s]

1it [00:00, 880.97it/s]

1it [00:00, 1708.47it/s]
 19%|█████▌                        | 103286/555588 [5:24:32<25:34:09,  4.91it/s]
1it [00:00, 1197.00it/s]

1it [00:00, 568.64it/s]
 19%|█████▌                        | 103288/555588 [5:24:33<35:52:19,  3.50it/s]
1it [00:00, 1471.17it/s]

1it [00:00, 1298.55it/s]

1it [00:00, 1555.75it/s]
 19%|█████▌                        | 103291/555588 [5:24:34<25:05:50,  5.01it/s]
1it [00:00, 1651.30it/s]

1it [00:00, 1187.85it/s]
 19%|█████▌                        | 103293/555588 [5:24:34<32:08:36,  3.91it/s]
1it [00:00, 1428.58it/s]

1it [00:00, 1129.93it/s]
 19

In [ ]:
len(p_keywords)

In [106]:
len(p_keywords)

555588

In [100]:
p_keywords

[0    대통령, 라며, 개혁, 녹색, 일자리, 정부, 지원, 강조, 산업, 제정부
 Name: Keywords, dtype: object,
 0    원내대표, 협상, 홍준표, 회담, 문국현, 오늘, 국회, 인정, 민주당, 교섭단체
 Name: Keywords, dtype: object,
 0    앵커, 생각, 대해, 방송, 출신, 비판, 현장, 뉴스, 사실, 발언
 Name: Keywords, dtype: object,
 0    언론사, 일부, 현재, 앵커, 보도, 재벌, 언론, 관련, 김주하, 파업
 Name: Keywords, dtype: object,
 0    의원, 국회, 블로그, 경위, 민주당, 본회의, 최문순, 모습, 사진, 현장
 Name: Keywords, dtype: object,
 0    비상, 경제, 회의, 대책, 상황, 대통령, 황실, 대변인, 제정부, 청와대
 Name: Keywords, dtype: object,
 0    발행, 지방자치단체, 선관위, 공직선거법, 관계자, 내용, 소식지, 홍보, 구청, 실적
 Name: Keywords, dtype: object,
 0    국회, 보도, 기자, 민주당, 경찰, 충돌, 의원, 사무, 투입, 직권상정
 Name: Keywords, dtype: object,
 0    민주당, 국민, 본회의, 대표, 법안, 처리, 농성, 민생, 한나라당, 악법
 Name: Keywords, dtype: object,
 0    지난, 대통령, 선거, 대운하, 폐기, 진보, 언론, 공약, 사수, 분야
 Name: Keywords, dtype: object]

In [101]:
len(p_keywords)

10

In [102]:
type(p_keywords)

list

In [108]:
p_keywords[:10]

[0    대통령, 라며, 개혁, 녹색, 일자리, 정부, 지원, 강조, 산업, 제정부
 Name: Keywords, dtype: object,
 0    원내대표, 협상, 홍준표, 회담, 문국현, 오늘, 국회, 인정, 민주당, 교섭단체
 Name: Keywords, dtype: object,
 0    앵커, 생각, 대해, 방송, 출신, 비판, 현장, 뉴스, 사실, 발언
 Name: Keywords, dtype: object,
 0    언론사, 일부, 현재, 앵커, 보도, 재벌, 언론, 관련, 김주하, 파업
 Name: Keywords, dtype: object,
 0    의원, 국회, 블로그, 경위, 민주당, 본회의, 최문순, 모습, 사진, 현장
 Name: Keywords, dtype: object,
 0    비상, 경제, 회의, 대책, 상황, 대통령, 황실, 대변인, 제정부, 청와대
 Name: Keywords, dtype: object,
 0    발행, 지방자치단체, 선관위, 공직선거법, 관계자, 내용, 소식지, 홍보, 구청, 실적
 Name: Keywords, dtype: object,
 0    국회, 보도, 기자, 민주당, 경찰, 충돌, 의원, 사무, 투입, 직권상정
 Name: Keywords, dtype: object,
 0    민주당, 국민, 본회의, 대표, 법안, 처리, 농성, 민생, 한나라당, 악법
 Name: Keywords, dtype: object,
 0    지난, 대통령, 선거, 대운하, 폐기, 진보, 언론, 공약, 사수, 분야
 Name: Keywords, dtype: object]

In [109]:
type(p_keywords[0])

pandas.core.series.Series

In [110]:
a = p_keywords[0]

In [111]:
a_list = a.to_list()

In [112]:
type(a_list)

list

In [113]:
a_list

['대통령, 라며, 개혁, 녹색, 일자리, 정부, 지원, 강조, 산업, 제정부']

In [114]:
len(a_list)

1

In [115]:
keyword_list = []

for s in tqdm(p_keywords) :
    sl = s.to_list()
    ss = sl[0].split(', ')     
    keyword_list.append(ss)

100%|█████████████████████████████████| 555588/555588 [04:13<00:00, 2191.16it/s]


In [116]:
keyword_list[:10]

[['대통령', '라며', '개혁', '녹색', '일자리', '정부', '지원', '강조', '산업', '제정부'],
 ['원내대표', '협상', '홍준표', '회담', '문국현', '오늘', '국회', '인정', '민주당', '교섭단체'],
 ['앵커', '생각', '대해', '방송', '출신', '비판', '현장', '뉴스', '사실', '발언'],
 ['언론사', '일부', '현재', '앵커', '보도', '재벌', '언론', '관련', '김주하', '파업'],
 ['의원', '국회', '블로그', '경위', '민주당', '본회의', '최문순', '모습', '사진', '현장'],
 ['비상', '경제', '회의', '대책', '상황', '대통령', '황실', '대변인', '제정부', '청와대'],
 ['발행', '지방자치단체', '선관위', '공직선거법', '관계자', '내용', '소식지', '홍보', '구청', '실적'],
 ['국회', '보도', '기자', '민주당', '경찰', '충돌', '의원', '사무', '투입', '직권상정'],
 ['민주당', '국민', '본회의', '대표', '법안', '처리', '농성', '민생', '한나라당', '악법'],
 ['지난', '대통령', '선거', '대운하', '폐기', '진보', '언론', '공약', '사수', '분야']]

In [117]:
df.columns

Index(['id', 'topic', 'text', 'keywords'], dtype='object')

In [118]:
df['keywords_tfid'] = keyword_list

In [119]:
df = df.rename(columns={'keywords': 'keywords_textrank'})

In [120]:
df.columns

Index(['id', 'topic', 'text', 'keywords_textrank', 'keywords_tfid'], dtype='object')

In [121]:
df[:10]

id topic  \
0   NIRW1900000001.37    정치   
1   NIRW1900000001.58    정치   
2   NIRW1900000001.60    정치   
3  NIRW1900000001.103    정치   
4  NIRW1900000001.120    정치   
5  NIRW1900000001.150    정치   
6  NIRW1900000001.157    정치   
7  NIRW1900000001.171    정치   
8  NIRW1900000001.198    정치   
9  NIRW1900000001.213    정치   

                                                text  \
0  이명박 대통령, '비상경제정부' 선언 이명박 대통령이 '비상경제정부'를 선언하고 나...   
1  홍준표는 왜 회담장을 박차고 나왔나 국회 대치정국을 풀기 위한 여야의 최후 담판 과...   
2  "저널리즘 차원에서 중요한 사건틀리다고 생각했다면 말도 안 했다" MBC <뉴스데스...   
3  "MBC가 일부 재벌과 언론사 소유가 된다면..." <뉴스데스크> 박혜진 아나운서,...   
4  문순씨네 블로그? 국회의원도 현장중계 국회의원도 이젠 블로거? 최문순 의원이 만든 ...   
5  MB의 '비상경제정부' 윤곽 드러나다 이명박 정부가 경제위기를 조기에 극복하기 위해...   
6  자치단체 소식지, 선거법 위반 논란 대전시와 각 구청에서 발행하는 소식지(홍보물)는...   
7  KBS, '경인운하 경제성 있다'는 정부 입장 힘 실어 1. 방송3사, 국회 파행 ...   
8  민주당, 12일만에 본회의장 농성 해제 민주당 12일만에 본회의장 농성 해제 민주당...   
9  이문열 "권력 놓은 홍위병들, 각 분야에서 저항" 대표적인 보수논객 작가 이문열씨가...   

                                   keywords_textrank  \
0  ['대통령', '정부', '녹색', '개혁', '지원', '일자리', '라며', '...   
1  ['원내대표', '협상', '홍준표', '회담', '문국현', '국회', '인정',...   
2  ['앵커', '생각', '대해', '출신', '방송', '뉴스', '사실', '비판...   
3  ['언론사', '일부', '앵커', '현재', '재벌', '김주하', '보도', '...   
4  ['의원', '블로그', '국회', '최문순', '민주당', '모습', '본회의',...   
5  ['비상', '경제', '대책', '회의', '상황', '대통령', '황실', '실...   
6  ['발행', '관계자', '소식지', '홍보', '구청', '별로', '문제', '...   
7  ['국회', '보도', '기자', '민주당', '경찰', '사무', '투입', '상...   
8  ['민주당', '국민', '대표', '본회의', '법안', '한나라당', '민생',...   
9  ['지난', '분야', '공약', '대해', '선거', '대통령', '언론', '폐...   

                                       keywords_tfid  
0        [대통령, 라며, 개혁, 녹색, 일자리, 정부, 지원, 강조, 산업, 제정부]  
1    [원내대표, 협상, 홍준표, 회담, 문국현, 오늘, 국회, 인정, 민주당, 교섭단체]  
2           [앵커, 생각, 대해, 방송, 출신, 비판, 현장, 뉴스, 사실, 발언]  
3         [언론사, 일부, 현재, 앵커, 보도, 재벌, 언론, 관련, 김주하, 파업]  
4       [의원, 국회, 블로그, 경위, 민주당, 본회의, 최문순, 모습, 사진, 현장]  
5       [비상, 경제, 회의, 대책, 상황, 대통령, 황실, 대변인, 제정부, 청와대]  
6  [발행, 지방자치단체, 선관위, 공직선거법, 관계자, 내용, 소식지, 홍보, 구청,...  
7        [국회, 보도, 기자, 민주당, 경찰, 충돌, 의원, 사무, 투입, 직권상정]  
8       [민주당, 국민, 본회의, 대표, 법안, 처리, 농성, 민생, 한나라당, 악법]  
9         [지난, 대통령, 선거, 대운하, 폐기, 진보, 언론, 공약, 사수, 분야]

In [122]:
row = df.iloc[0]

In [123]:
row

id                                                   NIRW1900000001.37
topic                                                               정치
text                 이명박 대통령, '비상경제정부' 선언 이명박 대통령이 '비상경제정부'를 선언하고 나...
keywords_textrank    ['대통령', '정부', '녹색', '개혁', '지원', '일자리', '라며', '...
keywords_tfid              [대통령, 라며, 개혁, 녹색, 일자리, 정부, 지원, 강조, 산업, 제정부]
Name: 0, dtype: object

In [124]:
type(row.keywords_textrank)

str

In [125]:
type(row.keywords_tfid)

list

In [132]:
df['keywords_textrank'] = df['keywords_textrank'].apply(string_to_list)

In [135]:
type(df.iloc[0].keywords_textrank)

list

In [134]:
df.to_csv(directory_path+'/news_P_two_keywords.tsv', sep='\t', index=False)

In [136]:
df[:10]

id topic  \
0   NIRW1900000001.37    정치   
1   NIRW1900000001.58    정치   
2   NIRW1900000001.60    정치   
3  NIRW1900000001.103    정치   
4  NIRW1900000001.120    정치   
5  NIRW1900000001.150    정치   
6  NIRW1900000001.157    정치   
7  NIRW1900000001.171    정치   
8  NIRW1900000001.198    정치   
9  NIRW1900000001.213    정치   

                                                text  \
0  이명박 대통령, '비상경제정부' 선언 이명박 대통령이 '비상경제정부'를 선언하고 나...   
1  홍준표는 왜 회담장을 박차고 나왔나 국회 대치정국을 풀기 위한 여야의 최후 담판 과...   
2  "저널리즘 차원에서 중요한 사건틀리다고 생각했다면 말도 안 했다" MBC <뉴스데스...   
3  "MBC가 일부 재벌과 언론사 소유가 된다면..." <뉴스데스크> 박혜진 아나운서,...   
4  문순씨네 블로그? 국회의원도 현장중계 국회의원도 이젠 블로거? 최문순 의원이 만든 ...   
5  MB의 '비상경제정부' 윤곽 드러나다 이명박 정부가 경제위기를 조기에 극복하기 위해...   
6  자치단체 소식지, 선거법 위반 논란 대전시와 각 구청에서 발행하는 소식지(홍보물)는...   
7  KBS, '경인운하 경제성 있다'는 정부 입장 힘 실어 1. 방송3사, 국회 파행 ...   
8  민주당, 12일만에 본회의장 농성 해제 민주당 12일만에 본회의장 농성 해제 민주당...   
9  이문열 "권력 놓은 홍위병들, 각 분야에서 저항" 대표적인 보수논객 작가 이문열씨가...   

                                keywords_textrank  \
0     [대통령, 정부, 녹색, 개혁, 지원, 일자리, 라며, 제정부, 비상, 또한]   
1  [원내대표, 협상, 홍준표, 회담, 문국현, 국회, 인정, 교섭단체, 얼굴, 오늘]   
2        [앵커, 생각, 대해, 출신, 방송, 뉴스, 사실, 비판, 파업, 발언]   
3     [언론사, 일부, 앵커, 현재, 재벌, 김주하, 보도, 파업, 우리, 인터뷰]   
4    [의원, 블로그, 국회, 최문순, 민주당, 모습, 본회의, 경위, 사진, 상황]   
5     [비상, 경제, 대책, 회의, 상황, 대통령, 황실, 실장, 대변인, 청와대]   
6  [발행, 관계자, 소식지, 홍보, 구청, 별로, 문제, 추진, 선관위, 공직선거법]   
7       [국회, 보도, 기자, 민주당, 경찰, 사무, 투입, 상황, 의원, 충돌]   
8    [민주당, 국민, 대표, 본회의, 법안, 한나라당, 민생, 처리, 악법, 농성]   
9      [지난, 분야, 공약, 대해, 선거, 대통령, 언론, 폐기, 동안, 홍위병]   

                                       keywords_tfid  
0        [대통령, 라며, 개혁, 녹색, 일자리, 정부, 지원, 강조, 산업, 제정부]  
1    [원내대표, 협상, 홍준표, 회담, 문국현, 오늘, 국회, 인정, 민주당, 교섭단체]  
2           [앵커, 생각, 대해, 방송, 출신, 비판, 현장, 뉴스, 사실, 발언]  
3         [언론사, 일부, 현재, 앵커, 보도, 재벌, 언론, 관련, 김주하, 파업]  
4       [의원, 국회, 블로그, 경위, 민주당, 본회의, 최문순, 모습, 사진, 현장]  
5       [비상, 경제, 회의, 대책, 상황, 대통령, 황실, 대변인, 제정부, 청와대]  
6  [발행, 지방자치단체, 선관위, 공직선거법, 관계자, 내용, 소식지, 홍보, 구청,...  
7        [국회, 보도, 기자, 민주당, 경찰, 충돌, 의원, 사무, 투입, 직권상정]  
8       [민주당, 국민, 본회의, 대표, 법안, 처리, 농성, 민생, 한나라당, 악법]  
9         [지난, 대통령, 선거, 대운하, 폐기, 진보, 언론, 공약, 사수, 분야]

In [137]:
keywords_set = []

for row in df.iterrows():
    keywords_set.append(set(row[1]['keywords_textrank'] + row[1]['keywords_tfid']))

In [138]:
df['keywords'] = keywords_set

In [139]:
file_path = '/home/osung/data/korean/KSIC_keyword.txt'
KSIC_S_keywords = parse_text_file(file_path)

In [140]:
combined_list = []

for key in KSIC_S_keywords :
    combined_list.extend(KSIC_S_keywords[key])

In [141]:
# 각 행에 대해 일치하는 문자열의 개수를 세고 새로운 열에 저장
df['match_count'] = df['keywords'].apply(lambda x: count_matches(x, combined_list))

In [142]:
df = df.sort_values(by='match_count', ascending=False)

In [143]:
df[:300]

id topic  \
549367   NWRW2200000004.5455    정치   
104415  NWRW1900000016.22077    정치   
549382   NWRW2200000004.5583    정치   
547494  NWRW2200000003.19451    정치   
417129  NWRW1900000008.25815    정치   
...                      ...   ...   
309158  NPRW1900000066.16315    정치   
115697   NLRW1900000047.3535    정치   
521369   NWRW2100000001.5552    정치   
9574     NIRW1900000007.4907    정치   
269155   NPRW1900000010.6213    정치   

                                                     text  \
549367  전기 비행기는 배터리가 너무 무거워… ‘수소 비행기’가 뜬다 ‘제트여객기 285g,...   
104415  동북아 오일허브 사업 5170억 들여 ‘빈 깡통’ 정부가 세계 4대 오일 허브로 키...   
549382  이마트 과일 용기 ‘재생 플라스틱’으로 교체 이마트가 6월부터 과일·채소를 포장하는...   
547494  경제외교 나선 삼성·현대차·SK·LG… 한미정상회담서 잭팟 노린다 삼성·현대자동차·...   
417129  CJ 손경식 ＂조원동(前 청와대 경제수석), 대통령 뜻이라며 이미경 물러나라 했다＂...   
...                                                   ...   
309158  철강-건설업계 '안전' 한목소리…정품 철강재 사용 강조 철강업계와 건설업계가 한자리...   
115697  ‘우주기업 시험센터 갈등’ 국회의원 싸움으로 확산 가칭 ‘우주기업 시험센터’ 유치를...   
521369  “쉴 수도 없고, 쉬어서도 안 된다”…연일 강행군 정세균 총리 정세균 국무총리가 대...   
9574    "최경환에게 전달된 'BH 요청' 쪽지, 대통령 아니면 누가?" 지난달 7일 최경환...   
269155  美 "남아도는 가스, 수출하겠다"…러시아에 에너지 패권 전쟁 선포 래리 커들로 백악...   

                                   keywords_textrank  \
549367   [수소, 비행기, 전기, 배터리, 연료, 전지, 기반, 모터, 항공기, 리튬]   
104415     [배럴, 오일, 저장, 허브, 유제품, 탱크, 사업, 석유, 원유, 해당]   
549382  [플라스틱, 용기, 재생, 포장, 라벨, 과일, 이마트, 스티커, 채소, 기존]   
547494  [미국, 투자, 생산, 전기차, 백신, 현대차, 공장, 삼성, 배터리, 반도체]   
417129    [회장, 최씨, 롯데, 의원, 스포츠, 재단, 광고, 회사, 현대차, 정유]   
...                                              ...   
309158      [건설, 품질, 안전, 철강, 관리, 사용, 의무, 현장, 강재, 품목]   
115697    [의원, 위원장, 진주, 예산, 김재경, 사천, 우주, 센터, 시험, 항공]   
521369    [총리, 코로나, 대구, 환자, 마스크, 경북, 수급, 상황, 현장, 직접]   
9574      [정부, 청와대, 대행, 쪽지, 총리, 내용, 병원, 메르스, 환자, 경유]   
269155   [러시아, 미국, 원유, 시장, 가스, 세계, 에너지, 생산량, 배럴, 수출]   

                                       keywords_tfid  \
549367   [수소, 비행기, 전기, 배터리, 연료, 전지, 기반, 모터, 리튬, 항공기]   
104415     [오일, 배럴, 허브, 사업, 저장, 탱크, 석유, 원유, 유제품, 여수]   
549382  [플라스틱, 용기, 재생, 이마트, 포장, 과일, 라벨, 사용, 스티커, 채소]   
547494  [미국, 투자, 생산, 전기차, 공장, 현대차, 전자, 반도체, 배터리, 백신]   
417129    [회장, 롯데, 최씨, 의원, 재단, 스포츠, 광고, 현대차, 한화, 회사]   
...                                              ...   
309158      [건설, 품질, 안전, 관리, 철강, 사용, 의무, 강재, 현장, 강화]   
115697  [의원, 진주, 예산, 위원장, 사천, 우주, 김재경, 사업, 국회의원, 산업]   
521369    [총리, 코로나, 대구, 환자, 마스크, 경북, 치료, 정부, 현장, 병상]   
9574      [청와대, 총리, 정부, 쪽지, 대행, 병원, 메르스, 라며, 내용, 요청]   
269155   [러시아, 미국, 가스, 시장, 원유, 세계, 에너지, 위원장, 수출, 배럴]   

                                                 keywords  match_count  
549367        {전기, 수소, 항공기, 배터리, 기반, 리튬, 전지, 연료, 모터, 비행기}            7  
104415      {배럴, 유제품, 석유, 탱크, 여수, 오일, 사업, 원유, 해당, 저장, 허브}            7  
549382   {이마트, 라벨, 과일, 포장, 용기, 스티커, 채소, 기존, 재생, 플라스틱, 사용}            7  
547494   {전자, 백신, 전기차, 공장, 배터리, 반도체, 현대차, 삼성, 생산, 미국, 투자}            6  
417129     {회장, 스포츠, 재단, 정유, 한화, 롯데, 현대차, 의원, 광고, 회사, 최씨}            6  
...                                                   ...          ...  
309158       {강화, 현장, 철강, 의무, 강재, 품질, 관리, 품목, 건설, 안전, 사용}            3  
115697  {사천, 센터, 위원장, 우주, 산업, 항공, 사업, 김재경, 진주, 의원, 예산,...            3  
521369  {마스크, 상황, 직접, 수급, 치료, 병상, 현장, 대구, 경북, 환자, 정부, ...            3  
9574    {쪽지, 대행, 내용, 청와대, 라며, 총리, 경유, 메르스, 환자, 정부, 요청,...            3  
269155   {시장, 배럴, 위원장, 러시아, 수출, 에너지, 가스, 생산량, 원유, 미국, 세계}            3  

[300 rows x 7 columns]

In [144]:
df.to_csv(directory_path+'/news_P_two_keywords.tsv', sep='\t', index=False)

In [146]:
# KSIC M(edium) Keywords 생성 
KSIC_M_keywords = {}

for key, value in KSIC_S_keywords.items():
    # key의 마지막 글자 제거
    new_key = key[:-1]
    
    # 기존에 존재하는 key라면 value 병합
    if new_key in KSIC_M_keywords:
        KSIC_M_keywords[new_key].extend(value)
    else:
        KSIC_M_keywords[new_key] = value

# 병합된 list에서 중복 제거
for key in KSIC_M_keywords:
    KSIC_M_keywords[key] = list(set(KSIC_M_keywords[key]))

In [147]:
KSIC_M_keywords

{'c10': ['찹쌀가루',
  '유산균음료',
  '쌀가루',
  '쥐포',
  '포도잼',
  '쌈무',
  '매실액',
  '사과즙',
  '두유',
  '약과',
  '미역',
  '선지',
  '오리고기',
  '간장',
  '농협',
  '오징어',
  '도정',
  '옥수수가루',
  '황태',
  '조미김',
  '갈비',
  '고구마말랭이',
  '생선까스',
  '유제품',
  '닭갈비',
  '과일주스',
  '정제유',
  '해삼',
  '한우',
  '콩가루',
  '축산물',
  '채소주스',
  '우유',
  '어육',
  '가리비',
  '육류',
  '소시지',
  '배즙',
  '케첩',
  '베이킹파우더',
  '돈가스',
  '반죽',
  '음식물',
  '연유',
  '양파',
  '스파게티',
  '수프',
  '도시락',
  '유업',
  '정비',
  '광어',
  '마리',
  '단무지',
  '갈치',
  '비스킷',
  '도미',
  '콘플레이크',
  '줄돔',
  '피클',
  '크래커',
  '방앗간',
  '김치',
  '된장',
  '수산물',
  '양계',
  '도축장',
  '사육',
  '제분소',
  '글루텐',
  '녹차',
  '딸기잼',
  '원유',
  '관상어',
  '이스트',
  '무쌈',
  '도축',
  '치즈',
  '해조',
  '정미소',
  '햄스터',
  '베이커리',
  '생선가스',
  '농축유',
  '조미료',
  '설탕',
  '농가',
  '발효유',
  '타피오카',
  '콩기름',
  '물엿',
  '라이스페이퍼',
  '토종닭',
  '포도당',
  '건채소',
  '반려',
  '구운김',
  '개껌',
  '어묵',
  '케이크',
  '동물',
  '석화',
  '농업',
  '항만',
  '가자미',
  '건강원',
  '캐비어',
  '장아찌',
  '멍게',
  '떡고물',
  '떡',
  '마요네즈',
  '액젓',
  '닭꼬치',
  '사과

In [149]:
match_S_list = []

for index, row in tqdm(df.iterrows()):
    match_S_list.append(count_keyword_matches(row['keywords'], KSIC_S_keywords))

555588it [03:45, 2465.25it/s]


In [150]:
match_M_list = []

for index, row in tqdm(df.iterrows()):
    match_M_list.append(count_keyword_matches(row['keywords'], KSIC_M_keywords))

555588it [02:54, 3179.62it/s]


In [151]:
max_S_ksic = []

for match in tqdm(match_S_list) :
    max_S_ksic.append(get_max_ksic(match))

100%|█████████████████████████████████| 555588/555588 [01:46<00:00, 5209.82it/s]


In [152]:
max_M_ksic = []

for match in tqdm(match_M_list) :
    max_M_ksic.append(get_max_ksic(match))

100%|█████████████████████████████████| 555588/555588 [01:50<00:00, 5036.40it/s]


In [153]:
df['match_S_list'] = match_S_list
df['match_M_list'] = match_M_list
df['max_S_ksic'] = max_S_ksic
df['max_M_ksic'] = max_M_ksic

In [154]:
df.to_csv(directory_path+'/news_P_KSIC_keywords.tsv', sep='\t', index=False)